# Standalone with Detailed Downstream Modeling Example

In [11]:
from generation_models import StandaloneStorageModel, ACLosses, BaseSystemDesign, DownstreamSystem, MultiStorageInputs, BatteryParams, DARTPrices, Transformer
from tyba_client.client import Client
import numpy as np
import pandas as pd
import os

In [3]:
client = Client(os.environ["TYBA_PAT"])

## Build model, including DownstreamSystem

In [12]:
model = StandaloneStorageModel(
    energy_prices=DARTPrices(
        dam=np.random.random(720).tolist(),
        rtm=np.random.random(720).tolist(),
    ),
    storage_inputs=MultiStorageInputs(
        batteries=[BatteryParams(
            power_capacity=2e3,
            energy_capacity=4e3 / 0.95,
            discharge_efficiency=0.95,
            charge_efficiency=0.05,
            degradation_rate=0.04,
        )],
    ),
    downstream_system=DownstreamSystem(
        losses=ACLosses(
            ac_wiring=0.015,
            transmission=0.012,
            mv_transformer=Transformer(load_loss=0.01, no_load_loss=0.003),
            hv_transformer=Transformer(load_loss=0.009, no_load_loss=0.004),
        ),
        system_design=BaseSystemDesign(dc_capacity=2e3, ac_capacity=2.5e3, poi_limit=2e3),
        model_losses_from="DC",
        inverter="SMA America: SWR2500U [240V]",
    ),
    project_term=720,
    project_term_units="hours",
)

## Run model

In [13]:
resp = client.schedule(model)

In [15]:
id_ = resp.json()["id"]

In [17]:
res = client.wait_on_result(id_)

## Check out results

In [25]:
res.keys()

dict_keys(['system', 'optimizer_outputs', 'market_awards'])

In [19]:
system, optimizer, awards = (pd.DataFrame(v) for v in res.values())

In [22]:
system  # analogous to the usual solar_storage

hv_xfmr_no_load_loss         gen  ...  mv_xfmr_no_load_loss  ac_wiring_loss
0                     8.0    -8.00000  ...                   6.0           0.000
1                     8.0    -8.00000  ...                   6.0           0.000
2                     8.0    -8.00000  ...                   6.0           0.000
3                     8.0    -8.00000  ...                   6.0           0.000
4                     8.0    -8.00000  ...                   6.0           0.000
..                    ...         ...  ...                   ...             ...
715                   8.0    -8.00000  ...                   6.0           0.000
716                   8.0 -2056.54405  ...                   6.0          30.000
717                   8.0    84.50917  ...                   6.0           1.425
718                   8.0    -8.00000  ...                   6.0           0.000
719                   8.0    -8.00000  ...                   6.0           0.000

[720 rows x 26 columns]

In [23]:
optimizer  # same as in hybrid

storage_discharge_max  charge_lo  ...  rtm_discharge  soe_lo_hb
0                   2000.0        0.0  ...            0.0        0.0
1                   2000.0        0.0  ...            0.0        0.0
2                   2000.0        0.0  ...            0.0        0.0
3                   2000.0        0.0  ...            0.0        0.0
4                   2000.0        0.0  ...            0.0        0.0
..                     ...        ...  ...            ...        ...
715                 2000.0        0.0  ...            0.0        0.0
716                 2000.0     2000.0  ...            0.0        0.0
717                 2000.0        0.0  ...           95.0      100.0
718                 2000.0        0.0  ...            0.0        0.0
719                 2000.0        0.0  ...            0.0        0.0

[720 rows x 34 columns]

In [24]:
awards  # optimizer results after offer correction

negative_dam_base_point  rtm_base_point  ...  rtm_charge  rtm_discharge
0                    0.00000         0.00000  ...     0.00000        0.00000
1                    0.00000         0.00000  ...     0.00000        0.00000
2                    0.00000         0.00000  ...     0.00000        0.00000
3                    0.00000         0.00000  ...     0.00000        0.00000
4                    0.00000         0.00000  ...     0.00000        0.00000
..                       ...             ...  ...         ...            ...
715                  0.00000         0.00000  ...     0.00000        0.00000
716               2056.54405     -2056.54405  ...  2056.54405        0.00000
717                -84.50917        84.50917  ...     0.00000       84.50917
718                  0.00000         0.00000  ...     0.00000        0.00000
719                  0.00000         0.00000  ...     0.00000        0.00000

[720 rows x 13 columns]